# Segmenting & Clustering Neighborhoods in Toronto

## Part 1 of 3 - Retrieve & normalize data

**The data is available as a Wikipedia HTML page & the page source reveals a Table Structure (Column headings & data for each row)**

```
<tbody>
<tr>
<th>Postcode</th>
<th>Borough</th>
<th>Neighborhood
</th>
</tr>

................

<tr>
<td>M3A</td>
<td><a href="/wiki/North_York" title="North York">North York</a></td>
<td><a href="/wiki/Parkwoods" title="Parkwoods">Parkwoods</a>
</td>
</tr>

<tr>
<td>M4A</td>
<td><a href="/wiki/North_York" title="North York">North York</a></td>
<td><a href="/wiki/Victoria_Village" title="Victoria Village">Victoria Village</a>
</td>
</tr>

................

</tbody>

```

In [3]:
# import the libraries
import requests                     # Import requsts library that allows us to invoke a Web service
from bs4 import BeautifulSoup       # Utilize BeautifulSoup to parse & select data 
import pandas as pd                 # Utilize pandas DataFrame to store the retrieved table from Web scraping

# retrieve data using requests.get('url')
data = requests.get('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')


**Utilize BeautifulSoup HTML parser to retrieve the markup document & store it in a 'soup' variable**

In [4]:
# load the data into a soup variable
soup = BeautifulSoup(data.text, 'html.parser')  # Copy the HTML document to a soup variable
tbody  = soup.find('tbody')                     # Use the embedded table body (HTML tag tbody) & retrieve the table

# Optionally print the tbody to console to visualize the HTML representation of the table
#print(tbody)

**Iterate thru the body of the table & retrieve all the rows**

In [5]:
# Create a list called table[] to store the extracted values from the HTML table
table = []

# Copy the headings & data to the table
#for tr in tbody.find_all('tr'):
#    headings = [th.text for th in tr.find_all('th')]
#    table.append(headings)
#    values   = [tr.text for td in tr.find_all('td')]
#    table.append(values)

for tr in tbody.find_all('tr'):
    values   = [tr.text for td in tr.find_all('td')]  # Retrieve column values using HTML table data tag
    #values   = [tr.text for td in tr.find_all('a')]  # Retrieve column values using HTML attribute tag
    table.append(values)

# Display the number of rows retrieved from the table
print("\nTotal number of rows retrieved from the HTML table = ", len(table))

# Optionally print the raw table to the console 
#print(table)


Total number of rows retrieved from the HTML table =  288


**Cleanup the Table; Remove Empty lists, substitute newline '\n' characters with commas**

In [6]:
# Remove empty lists, tuples, zeroes, strings
table = [x for x in table if x != []]

# Print the cleaned table to the console
print("\nTotal number of rows retained from the HTML table = ", len(table))
#print(table)

# Create 
cleanTable = []

#for lst in table:
#    for element in lst:
#        if element not in cleanTable:
#                cleanTable.append(element)

for i in range(len(table)):
#    #print(table[i][0])
    cleanTable.append([str.replace(table[i][0], '\n', ',')])

# Print the cleaned table to the console
print("\nTotal number of rows in the cleaned version table = ", len(cleanTable))
#print(cleanTable)



Total number of rows retained from the HTML table =  287

Total number of rows in the cleaned version table =  287


**Copy the cleaned table (list of lists) to a DataFrame & clean up the same**

In [7]:
# Parse the cleanTable & split the comma separated values & create a dataframe

locDataFrame = pd.DataFrame()

for listItem in cleanTable:
    locDataFrame = locDataFrame.append(pd.DataFrame([sub.split(",") for sub in listItem]))

# Rename the Columns from default index (a number) to desired column names 1. Postcode 2. Borough 3. Neighborhood
locDataFrame.rename(columns={1:'Postcode', 2:'Borough', 3:'Neighborhood'}, inplace=True)

# Drop the 1st & last columns that don't have any values
locDataFrame.drop(columns=[0,4], inplace=True)

# Sort the Dataframe by Postcode, then by Borough, & by Neighborhood
locDataFrame.sort_values(['Postcode', 'Borough', 'Neighborhood'], axis=0, inplace = True)

# Rest the index (it'll insert a column named 'index' & assign the indexed values to the 'index' )
locDataFrame.reset_index(inplace=True)

# Drop the index column of DataFrame since they are all zeroes anyway
locDataFrame.drop(columns=['index'], inplace=True)

# Drop the rows that do not have an assigned 'Borough' name & copy it to a new location DataFrame
nlDataFrame = locDataFrame[locDataFrame['Borough'] != 'Not assigned'] 

print("\nTotal number of rows filtered (after removing ones with no Borough names)  ==> ", len(nlDataFrame))

# Print all the rows that contain 'Not assigned' (also a sanity check for any Burroughs that slipped thru)
print("\n\n== Rows with unassigned Neighborhood names ==\n\n", nlDataFrame[nlDataFrame.eq('Not assigned').any(1)])



Total number of rows filtered (after removing ones with no Borough names)  ==>  210


== Rows with unassigned Neighborhood names ==

     Postcode       Borough  Neighborhood
249      M9A  Queen's Park  Not assigned


**Fix the unassigned values, and aggregate all the Neighborhood by Postcode & Borough**  

In [8]:
# Loop through the dataframe, copy the Borough name to Neighborhood name if the latter is unassigned
for idx in nlDataFrame.index:
    if(nlDataFrame['Neighborhood'].at[idx] == 'Not assigned'):
        print("\nBorough name of the unassigned neighborhood ( at index",idx,") ==> ", nlDataFrame['Borough'].at[idx])
        nlDataFrame['Neighborhood'].at[idx] = nlDataFrame['Borough'].at[idx]
        print("\nNeighborhood name reset to the Borough name ( at index",idx,") ==> ", nlDataFrame['Neighborhood'].at[idx])


# Display the head of the dataframe (notice it's automatically sorted by 'Postcode')
#df_filtered.head()
        
#############################################################################################################
# CONSOLIDATE THE DATAFRAME BY AGGREGATING NEIGHBORHOOD VALUES, FOR EACH POSTCODE, FOLLOWED BY BOROUGHNAME
#############################################################################################################

nnlDataFrame = nlDataFrame.groupby(['Postcode', 'Borough']).agg(lambda col: ','.join(col))

# Reset the Index
nnlDataFrame.reset_index(inplace = True)

# Print the head of the new consolidated dataframe (first 12 rows)
nnlDataFrame.head(12)



Borough name of the unassigned neighborhood ( at index 249 ) ==>  Queen's Park

Neighborhood name reset to the Borough name ( at index 249 ) ==>  Queen's Park


Postcode      Borough                                       Neighborhood
0       M1B  Scarborough                                      Malvern,Rouge
1       M1C  Scarborough               Highland Creek,Port Union,Rouge Hill
2       M1E  Scarborough                    Guildwood,Morningside,West Hill
3       M1G  Scarborough                                             Woburn
4       M1H  Scarborough                                          Cedarbrae
5       M1J  Scarborough                                Scarborough Village
6       M1K  Scarborough          East Birchmount Park,Ionview,Kennedy Park
7       M1L  Scarborough                      Clairlea,Golden Mile,Oakridge
8       M1M  Scarborough      Cliffcrest,Cliffside,Scarborough Village West
9       M1N  Scarborough                         Birch Cliff,Cliffside West
10      M1P  Scarborough  Dorset Park,Scarborough Town Centre,Wexford He...
11      M1R  Scarborough                                   Maryvale,Wexford

**Summarize the unique Boroughs & Neighborhoods in Toronto***

In [9]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(nnlDataFrame['Borough'].unique()),
        nnlDataFrame.shape[0]
    )
)

The dataframe has 11 boroughs and 103 neighborhoods.


**Finally print the shape of the new DataFrame object (as required to show as final step)**

In [10]:
print("The Shape of the DataFrame is ==> ", nnlDataFrame.shape)

The Shape of the DataFrame is ==>  (103, 3)


## Part 2 of 3 - Enrich the Dataframe & analyze data

**Installation of geocoder package did not respond & hence the provided CSV file will be used for latitude & longitude info**
```
#!conda install -c conda-forge geocoder
#!conda install -c conda-forge/label/gcc7 geocoder
#!conda install -c conda-forge/label/cf201901 geocoder

#import geocoder # import geocoder

# initialize your variable to None
lat_lng_coords = None
postal_code = "M5G"
# loop until you get the coordinates
while(lat_lng_coords is None):
  g = geocoder.google('{}, Toronto, Ontario'.format(postal_code))
  lat_lng_coords = g.latlng

latitude = lat_lng_coords[0]
longitude = lat_lng_coords[1]

print (latitude, longitude)

```

**Retrieve the CSV file with Postal Code, Latitude & Longitude & read it into a pandas DataFrame**

In [11]:
# Read the CSV file into a pandas DataFrame
geoDataFrame = pd.read_csv('http://cocl.us/Geospatial_data')

# Display the head of the DataFrame
geoDataFrame.head()


Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

**Rename the 'Postal Code' to 'Postcode' so that the DataFrames can be joined on 'Postcode' as the key**

In [12]:
# Rename the key column of the DataFrame
geoDataFrame.rename(columns={'Postal Code':'Postcode'}, inplace=True)

# Display the head of the DataFrame with renamed column
geoDataFrame.head()


Postcode   Latitude  Longitude
0      M1B  43.806686 -79.194353
1      M1C  43.784535 -79.160497
2      M1E  43.763573 -79.188711
3      M1G  43.770992 -79.216917
4      M1H  43.773136 -79.239476

In [13]:
# Merge the DataFrames using Postcode as the key & create a final location DataFrame
flDataFrame = pd.merge(nnlDataFrame, geoDataFrame, on='Postcode')

# Display the shape of the Merged DataFrame (should be same as the shape of DataFrame constructed in part 1 of this exercise) 
print("The shape of the merged DataFrame is ==> ", flDataFrame.shape)

# Display the head (1st 12 rows) of the DatFrame 
flDataFrame.head(12)


The shape of the merged DataFrame is ==>  (103, 5)


Postcode      Borough                                       Neighborhood  \
0       M1B  Scarborough                                      Malvern,Rouge   
1       M1C  Scarborough               Highland Creek,Port Union,Rouge Hill   
2       M1E  Scarborough                    Guildwood,Morningside,West Hill   
3       M1G  Scarborough                                             Woburn   
4       M1H  Scarborough                                          Cedarbrae   
5       M1J  Scarborough                                Scarborough Village   
6       M1K  Scarborough          East Birchmount Park,Ionview,Kennedy Park   
7       M1L  Scarborough                      Clairlea,Golden Mile,Oakridge   
8       M1M  Scarborough      Cliffcrest,Cliffside,Scarborough Village West   
9       M1N  Scarborough                         Birch Cliff,Cliffside West   
10      M1P  Scarborough  Dorset Park,Scarborough Town Centre,Wexford He...   
11      M1R  Scarborough                                   Maryvale,Wexford   

     Latitude  Longitude  
0   43.806686 -79.194353  
1   43.784535 -79.160497  
2   43.763573 -79.188711  
3   43.770992 -79.216917  
4   43.773136 -79.239476  
5   43.744734 -79.239476  
6   43.727929 -79.262029  
7   43.711112 -79.284577  
8   43.716316 -79.239476  
9   43.692657 -79.264848  
10  43.757410 -79.273304  
11  43.750072 -79.295849

## Part 3 of 3 - Cluster neighborhoods by venue & visualize data on a Folium Map

**Lets us import libraries to plot, map, visualize & apply clustering algorithms**

In [14]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


**Use geopy library to get the latitude and longitude values of Toronto using geolocator & display the map using Folium**

In [15]:
# Assign Toronto, Ontario to an address variable 
address = 'Toronto, ON'

# Create a User Agent called toronto_explorer & assign it to a geolocator variable
geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

# Create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# Display the map of Toronto 
map_toronto

The geograpical coordinate of Toronto are 43.653963, -79.387207.


**Overlay the Folium Map created above with Boroughs & Neighborhoods of Tornoto & Display**

In [17]:
# Create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)

# Add Boroughs & Neighbors to the map above (remember to use the final DataFrame,  'flDataFrame' created in part 2 of exercise)
for lat, lng, borough, neighborhood in zip(flDataFrame['Latitude'], flDataFrame['Longitude'], flDataFrame['Borough'], flDataFrame['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    

In [18]:
map_toronto

In [19]:
# Double Check Obtain 43rd Neighborhood (Studio District)?
flDataFrame.loc[43, 'Neighborhood']

neighborhood_latitude = flDataFrame.loc[43, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = flDataFrame.loc[43, 'Longitude'] # neighborhood longitude value

neighborhood_name = flDataFrame.loc[43, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))


Latitude and longitude values of Studio District are 43.6595255, -79.340923.


**Invoke FourSquare API to get the venues near Studio District**

In [36]:
# Set the variables to invoke FourSquare API
CLIENT_ID = '---My Client Id---' # your Foursquare ID
CLIENT_SECRET = '---My Client Secret---' # your Foursquare Secret
VERSION = '20200103' # Foursquare API version

# type your answer here

search_query = neighborhood_name
latitude = neighborhood_latitude
longitude = neighborhood_longitude
radius = 500 # within 500 meters (units) - FourSquare uses metric units
LIMIT = 100  # get Top 100 venues

url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)

#print(url)

# Retrieve the results of a REST API call as a JSON string
results = requests.get(url).json()

results

{'meta': {'code': 200, 'requestId': '5e11aa31b4b684001b948abf'},
 'response': {'venues': [{'id': '4efcb570f9ab0847fa49c52e',
    'name': 'Toronto Studio District',
    'location': {'lat': 43.66337,
     'lng': -79.342353,
     'labeledLatLngs': [{'label': 'display',
       'lat': 43.66337,
       'lng': -79.342353}],
     'distance': 443,
     'cc': 'CA',
     'country': 'Canada',
     'formattedAddress': ['Canada']},
    'categories': [],
    'referralId': 'v-1578216067',
    'hasPerk': False},
   {'id': '4b72d297f964a5204e8a2de3',
    'name': 'Studio One Tattoo Supply',
    'location': {'address': '940 Queen Street E',
     'lat': 43.66062826043434,
     'lng': -79.34153081705182,
     'labeledLatLngs': [{'label': 'display',
       'lat': 43.66062826043434,
       'lng': -79.34153081705182}],
     'distance': 132,
     'postalCode': 'M4M 1J7',
     'cc': 'CA',
     'city': 'Toronto',
     'state': 'ON',
     'country': 'Canada',
     'formattedAddress': ['940 Queen Street E',
      '

**Extract the venues near Studio District from the JSON document using json_normalize()**

In [37]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# RETRIEVE VENUES FROM THE RESULTS STRING RETURED BY THE REST API
venues = results['response']['venues']

# CREATE A DATAFRAME USING JSON_NORMALIZE()
nearby_venues = json_normalize(venues)
nearby_venues.head(3)

# nearby_venues
# filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
filtered_columns = ['name', 'categories', 'location.lat', 'location.lng']
nearby_venues = nearby_venues.loc[:, filtered_columns]


print("There are ", len(nearby_venues), " venues near",neighborhood_name)

nearby_venues.head(3)


There are  40  venues near Studio District


name  \
0       Toronto Studio District   
1      Studio One Tattoo Supply   
2  Studio M Digital Productions   

                                          categories  location.lat  \
0                                                 []     43.663370   
1                                                 []     43.660628   
2  [{'id': '4bf58dd8d48988d124941735', 'name': 'O...     43.661819   

   location.lng  
0    -79.342353  
1    -79.341531  
2    -79.340728

**Get all the neighborhoods & venue categories in Toronto so that we have more than 40 data points for mapping**

**Define a complex function (provided by the instructor as a part of Lab exercise) to extract attributes of a venue**

In [ ]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

**Get all the venues & attributes in Totonto by invoking the above, getNearbyVenues function; flDataFrame is passed to the function**

In [24]:
toronto_venues = getNearbyVenues(names=flDataFrame['Neighborhood'],
                                   latitudes=flDataFrame['Latitude'],
                                   longitudes=flDataFrame['Longitude']
                                  )

# THE FUNCTION RETURNS A DATAFRAME & ALSO PRINTS EACH VENUE RETURNED TO THE CONSOLE
print("Number of Studio District Venues Returned = ", toronto_venues.size)
toronto_venues.head(3)

Malvern,Rouge
Highland Creek,Port Union,Rouge Hill
Guildwood,Morningside,West Hill
Woburn
Cedarbrae
Scarborough Village
East Birchmount Park,Ionview,Kennedy Park
Clairlea,Golden Mile,Oakridge
Cliffcrest,Cliffside,Scarborough Village West
Birch Cliff,Cliffside West
Dorset Park,Scarborough Town Centre,Wexford Heights
Maryvale,Wexford
Agincourt
Clarks Corners,Sullivan,Tam O'Shanter
Agincourt North,L'Amoreaux East,Milliken,Steeles East
L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview,Henry Farm,Oriole
Bayview Village
Silver Hills,York Mills
Newtonbrook,Willowdale
Willowdale South
York Mills West
Willowdale West
Parkwoods
Don Mills North
Don Mills South,Flemingdon Park
Bathurst Manor,Downsview North,Wilson Heights
Northwood Park,York University
CFB Toronto,Downsview East
Downsview West
Downsview Central
Downsview Northwest
Victoria Village
Parkview Hill,Woodbine Gardens
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto
Riverdale,The Danforth West
India Bazaar,The Beac

Neighborhood  Neighborhood Latitude  \
0                         Malvern,Rouge              43.806686   
1  Highland Creek,Port Union,Rouge Hill              43.784535   
2       Guildwood,Morningside,West Hill              43.763573   

   Neighborhood Longitude                            Venue  Venue Latitude  \
0              -79.194353                          Wendy's       43.807448   
1              -79.160497            Royal Canadian Legion       43.782533   
2              -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   

   Venue Longitude        Venue Category  
0       -79.199056  Fast Food Restaurant  
1       -79.163085                   Bar  
2       -79.189914           Pizza Place

**Group all Toronto Venues by Neighbourhood name & display counts of attributes**

In [25]:
toronto_venues.groupby('Neighborhood').count()


Neighborhood Latitude  \
Neighborhood                                                                
Adelaide,King,Richmond                                                100   
Agincourt                                                               4   
Agincourt North,L'Amoreaux East,Milliken,Steele...                      2   
Albion Gardens,Beaumond Heights,Humbergate,Jame...                      8   
Alderwood,Long Branch                                                   9   
Bathurst Manor,Downsview North,Wilson Heights                          21   
Bathurst Quay,CN Tower,Harbourfront West,Island...                     15   
Bayview Village                                                         4   
Bedford Park,Lawrence Manor East                                       24   
Berczy Park                                                            56   
Birch Cliff,Cliffside West                                              4   
Bloordale Gardens,Eringate,Markland Wood,Old Bu...                      8   
Brockton,Exhibition Place,Parkdale Village                             22   
Business Reply Mail Processing Centre 969 Eastern                      16   
CFB Toronto,Downsview East                                              2   
Cabbagetown,St. James Town                                             47   
Caledonia-Fairbanks                                                     5   
Canada Post Gateway Processing Centre                                  10   
Cedarbrae                                                               8   
Central Bay Street                                                     86   
Chinatown,Grange Park,Kensington Market                                91   
Christie                                                               17   
Church and Wellesley                                                   83   
Clairlea,Golden Mile,Oakridge                                          10   
Clarks Corners,Sullivan,Tam O'Shanter                                  10   
Cliffcrest,Cliffside,Scarborough Village West                           3   
Commerce Court,Victoria Hotel                                         100   
Davisville                                                             31   
Davisville North                                                        9   
Deer Park,Forest Hill SE,Rathnelly,South Hill,S...                     16   
Del Ray,Keelesdale,Mount Dennis,Silverthorn                             4   
Design Exchange,Toronto Dominion Centre                               100   
Don Mills North                                                         5   
Don Mills South,Flemingdon Park                                        22   
Dorset Park,Scarborough Town Centre,Wexford Hei...                      6   
Dovercourt Village,Dufferin                                            15   
Downsview Central                                                       2   
Downsview Northwest                                                     4   
Downsview West                                                          4   
Downsview,North Park,Upwood Park                                        4   
East Birchmount Park,Ionview,Kennedy Park                               5   
East Toronto                                                            4   
Emery,Humberlea                                                         3   
Fairview,Henry Farm,Oriole                                             64   
First Canadian Place,Underground city                                 100   
Forest Hill North,Forest Hill West                                      4   
Garden District,Ryerson                                               100   
Glencairn                                                               4   
Guildwood,Morningside,West Hill                                         8   
Harbord,University of Toronto                                          38   
Harbourfront                                    

**Perhaps the most important is to get a sense of all the Venue Categories; let's count & display**

In [26]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 267 uniques categories.


**Utilize ONE HOT ENCODING to represent all the categories of venues as 1s & 0s so that machines can compute the categorical data**

In [27]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

print(toronto_onehot.shape)

toronto_onehot.head()



(2227, 267)


Yoga Studio  Accessories Store  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Arts & Crafts Store  Asian Restaurant  \
0             0         0            0                    0                 0   
1             0         0            0                    0                 0   
2             0         0            0                    0                 0   
3             0         0            0                    0                 0   
4             0         0            0                    0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0                   0            0              0          0           0   
1                   0            0              0          0           0   
2                   0            0              0          0           0   
3                   0            0              0          0           0   
4                   0            0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    1               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    0               0                 0   

   Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  Beer Store  \
0                   0      0                0         0           0   
1                   0      0                0         0           0   
2                   0      0                0         0           0   
3                   0      0                0         0           0   
4                   0      0                0         0           0   

   Belgian Restaurant  Bike Shop  Bistro  Boat or Ferry  Bookstore  Boutique  \
0                   0          0       0              0          0         0   
1                   0          0       0              0          0         0   
2                   0          0       0              0          0         0   
3                   0          0       0              0          0         0   
4                   0          0       0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0             0              0         0   
2                0         0             0              0         0   
3                0         0             0              0         0   
4                0         0            

**Group the onehot encoded data by neighborhood, & by calculating mean occurance of the venue category**

In [28]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                              Adelaide,King,Richmond     0.000000   
1                                           Agincourt     0.000000   
2   Agincourt North,L'Amoreaux East,Milliken,Steel...     0.000000   
3   Albion Gardens,Beaumond Heights,Humbergate,Jam...     0.000000   
4                               Alderwood,Long Branch     0.000000   
5       Bathurst Manor,Downsview North,Wilson Heights     0.000000   
6   Bathurst Quay,CN Tower,Harbourfront West,Islan...     0.000000   
7                                     Bayview Village     0.000000   
8                    Bedford Park,Lawrence Manor East     0.000000   
9                                         Berczy Park     0.000000   
10                         Birch Cliff,Cliffside West     0.000000   
11  Bloordale Gardens,Eringate,Markland Wood,Old B...     0.000000   
12         Brockton,Exhibition Place,Parkdale Village     0.000000   
13  Business Reply Mail Processing Centre 969 Eastern     0.062500   
14                         CFB Toronto,Downsview East     0.000000   
15                         Cabbagetown,St. James Town     0.000000   
16                                Caledonia-Fairbanks     0.000000   
17              Canada Post Gateway Processing Centre     0.000000   
18                                          Cedarbrae     0.000000   
19                                 Central Bay Street     0.011628   
20            Chinatown,Grange Park,Kensington Market     0.000000   
21                                           Christie     0.000000   
22                               Church and Wellesley     0.024096   
23                      Clairlea,Golden Mile,Oakridge     0.000000   
24              Clarks Corners,Sullivan,Tam O'Shanter     0.000000   
25      Cliffcrest,Cliffside,Scarborough Village West     0.000000   
26                      Commerce Court,Victoria Hotel     0.000000   
27                                         Davisville     0.000000   
28                                   Davisville North     0.000000   
29  Deer Park,Forest Hill SE,Rathnelly,South Hill,...     0.000000   
30        Del Ray,Keelesdale,Mount Dennis,Silverthorn     0.000000   
31            Design Exchange,Toronto Dominion Centre     0.000000   
32                                    Don Mills North     0.000000   
33                    Don Mills South,Flemingdon Park     0.000000   
34  Dorset Park,Scarborough Town Centre,Wexford He...     0.000000   
35                        Dovercourt Village,Dufferin     0.000000   
36                                  Downsview Central     0.000000   
37                                Downsview Northwest     0.000000   
38                                     Downsview West     0.000000   
39                   Downsview,North Park,Upwood Park     0.000000   
40          East Birchmount Park,Ionview,Kennedy Park     0.000000   
41                                       East Toronto     0.000000   
42                                    Emery,Humberlea     0.000000   
43                         Fairview,Henry Farm,Oriole     0.000000   
44              First Canadian Place,Underground city     0.000000   
45                 Forest Hill North,Forest Hill West     0.000000   
46                            Garden District,Ryerson     0.000000   
47                                          Glencairn     0.000000   
48                    Guildwood,Morningside,West Hill     0.000000   
49                      Harbord,University of Toronto     0.000000   
50                                       Harbourfront     0.000000   
51    Harbourfront East,Toronto Islands,Union Station     0.000000   
52                       High Park,The Junction South     0.000000   
53               Highland Creek,Port Union,Rouge Hill     0.000000   
54                                  Hillcrest Village     0.000000   
55         Humber Bay Shores,Mimico South,New Toronto     0.000000   
56  Humber Bay,King's Mill Park,Kingsway Park Sout.

In [29]:
toronto_grouped.shape

(98, 267)

**Pick the Top 5 Venues in each neighborhood, based on the frequency of occurance of the venue categories**

**Store the values in a temporary dataframe**

In [30]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond----
              venue  freq
0       Coffee Shop  0.08
1              Café  0.05
2        Steakhouse  0.04
3               Bar  0.04
4  Sushi Restaurant  0.03


----Agincourt----
                       venue  freq
0                     Lounge  0.25
1             Breakfast Spot  0.25
2  Latin American Restaurant  0.25
3               Skating Rink  0.25
4           Malay Restaurant  0.00


----Agincourt North,L'Amoreaux East,Milliken,Steeles East----
                      venue  freq
0                      Park   0.5
1                Playground   0.5
2  Mediterranean Restaurant   0.0
3         Mobile Phone Shop   0.0
4        Miscellaneous Shop   0.0


----Albion Gardens,Beaumond Heights,Humbergate,Jamestown,Mount Olive,Silverstone,South Steeles,Thistletown----
                  venue  freq
0         Grocery Store  0.25
1  Fast Food Restaurant  0.12
2              Pharmacy  0.12
3           Pizza Place  0.12
4        Sandwich Place  0.12


----Alderwood,Long B

                venue  freq
0      Discount Store   0.4
1    Department Store   0.2
2         Bus Station   0.2
3         Coffee Shop   0.2
4  Mexican Restaurant   0.0


----East Toronto----
               venue  freq
0               Park  0.50
1  Convenience Store  0.25
2        Coffee Shop  0.25
3        Men's Store  0.00
4  Mobile Phone Shop  0.00


----Emery,Humberlea----
                           venue  freq
0  Paper / Office Supplies Store  0.33
1     Construction & Landscaping  0.33
2                 Baseball Field  0.33
3                    Yoga Studio  0.00
4       Mediterranean Restaurant  0.00


----Fairview,Henry Farm,Oriole----
                  venue  freq
0        Clothing Store  0.16
1  Fast Food Restaurant  0.08
2           Coffee Shop  0.08
3   Japanese Restaurant  0.05
4                Bakery  0.03


----First Canadian Place,Underground city----
         venue  freq
0  Coffee Shop  0.12
1         Café  0.07
2        Hotel  0.04
3   Restaurant  0.04
4          Gym  0

                      venue  freq
0                      Park  0.50
1                Playground  0.25
2                     Trail  0.25
3  Mediterranean Restaurant  0.00
4        Miscellaneous Shop  0.00


----Roselawn----
                             venue  freq
0                           Garden   1.0
1  Molecular Gastronomy Restaurant   0.0
2                           Lounge   0.0
3                 Malay Restaurant   0.0
4                           Market   0.0


----Runnymede,Swansea----
                venue  freq
0                Café  0.08
1         Coffee Shop  0.08
2  Italian Restaurant  0.05
3    Sushi Restaurant  0.05
4         Pizza Place  0.05


----Runnymede,The Junction North----
            venue  freq
0     Pizza Place   0.2
1  Breakfast Spot   0.2
2         Brewery   0.2
3   Grocery Store   0.2
4        Bus Line   0.2


----Scarborough Village----
                       venue  freq
0                        Spa   0.5
1                 Playground   0.5
2             Med

**Define a function to return the top most common categories of venues; how many can be passed to the function (example 10)**

In [ ]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

**Use numpy & pandas functions, and the above function to get TOP 10 venues in each neighborhood**

In [32]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood  \
0                             Adelaide,King,Richmond   
1                                          Agincourt   
2  Agincourt North,L'Amoreaux East,Milliken,Steel...   
3  Albion Gardens,Beaumond Heights,Humbergate,Jam...   
4                              Alderwood,Long Branch   

       1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                Coffee Shop                  Café            Steakhouse   
1  Latin American Restaurant        Breakfast Spot          Skating Rink   
2                       Park            Playground             Drugstore   
3              Grocery Store   Fried Chicken Joint              Pharmacy   
4                Pizza Place                  Pool                   Gym   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0                   Bar          Burger Joint            Restaurant   
1                Lounge   Dumpling Restaurant        Discount Store   
2    Dim Sum Restaurant                 Diner        Discount Store   
3        Sandwich Place           Pizza Place            Beer Store   
4          Skating Rink           Coffee Shop              Pharmacy   

  7th Most Common Venue 8th Most Common Venue        9th Most Common Venue  \
0       Thai Restaurant      Sushi Restaurant             Asian Restaurant   
1               Dog Run      Doner Restaurant                   Donut Shop   
2               Dog Run      Doner Restaurant                   Donut Shop   
3  Fast Food Restaurant     Electronics Store  Eastern European Restaurant   
4                   Pub        Sandwich Place                Women's Store   

          10th Most Common Venue  
0  Vegetarian / Vegan Restaurant  
1                      Drugstore  
2            Dumpling Restaurant  
3                   Dessert Shop  
4                   Dessert Shop

**Use K-Means of Sci-Kit Learn (sklearn) and fit the data to create data model & assign each venue to one of the 5 clusters** 

**The values of the clusters are pre determined (kclusters=5)**

In [33]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 


# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  \
0                         Malvern,Rouge              43.806686   
1  Highland Creek,Port Union,Rouge Hill              43.784535   
2       Guildwood,Morningside,West Hill              43.763573   
3       Guildwood,Morningside,West Hill              43.763573   
4       Guildwood,Morningside,West Hill              43.763573   

   Neighborhood Longitude                            Venue  Venue Latitude  \
0              -79.194353                          Wendy's       43.807448   
1              -79.160497            Royal Canadian Legion       43.782533   
2              -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   
3              -79.188711                G & G Electronics       43.765309   
4              -79.188711                       Marina Spa       43.766000   

   Venue Longitude        Venue Category  Cluster Labels  \
0       -79.199056  Fast Food Restaurant               4   
1       -79.163085                   Bar               3   
2       -79.189914           Pizza Place               0   
3       -79.191537     Electronics Store               0   
4       -79.191000                   Spa               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Fast Food Restaurant    Dim Sum Restaurant        Farmers Market   
1                   Bar         Women's Store   Dumpling Restaurant   
2   Rental Car Location                   Spa        Breakfast Spot   
3   Rental Car Location                   Spa        Breakfast Spot   
4   Rental Car Location                   Spa        Breakfast Spot   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0    Falafel Restaurant           Event Space  Ethiopian Restaurant   
1        Discount Store               Dog Run      Doner Restaurant   
2     Electronics Store           Pizza Place    Mexican Restaurant   
3     Electronics Store           Pizza Place    Mexican Restaurant   
4     Electronics Store           Pizza Place    Mexican Restaurant   

  7th Most Common Venue 8th Most Common Venue        9th Most Common Venue  \
0   Empanada Restaurant     Electronics Store  Eastern European Restaurant   
1            Donut Shop             Drugstore  Eastern European Restaurant   
2        Medical Center          Intersection                Women's Store   
3        Medical Center          Intersection                Women's Store   
4        Medical Center          Intersection                Women's Store   

  10th Most Common Venue  
0    Dumpling Restaurant  
1               Festival  
2                Dog Run  
3                Dog Run  
4                Dog Run

In [34]:
# add clustering labels
#neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  \
0                         Malvern,Rouge              43.806686   
1  Highland Creek,Port Union,Rouge Hill              43.784535   
2       Guildwood,Morningside,West Hill              43.763573   
3       Guildwood,Morningside,West Hill              43.763573   
4       Guildwood,Morningside,West Hill              43.763573   

   Neighborhood Longitude                            Venue  Venue Latitude  \
0              -79.194353                          Wendy's       43.807448   
1              -79.160497            Royal Canadian Legion       43.782533   
2              -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   
3              -79.188711                G & G Electronics       43.765309   
4              -79.188711                       Marina Spa       43.766000   

   Venue Longitude        Venue Category  Cluster Labels  \
0       -79.199056  Fast Food Restaurant               4   
1       -79.163085                   Bar               3   
2       -79.189914           Pizza Place               0   
3       -79.191537     Electronics Store               0   
4       -79.191000                   Spa               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Fast Food Restaurant    Dim Sum Restaurant        Farmers Market   
1                   Bar         Women's Store   Dumpling Restaurant   
2   Rental Car Location                   Spa        Breakfast Spot   
3   Rental Car Location                   Spa        Breakfast Spot   
4   Rental Car Location                   Spa        Breakfast Spot   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0    Falafel Restaurant           Event Space  Ethiopian Restaurant   
1        Discount Store               Dog Run      Doner Restaurant   
2     Electronics Store           Pizza Place    Mexican Restaurant   
3     Electronics Store           Pizza Place    Mexican Restaurant   
4     Electronics Store           Pizza Place    Mexican Restaurant   

  7th Most Common Venue 8th Most Common Venue        9th Most Common Venue  \
0   Empanada Restaurant     Electronics Store  Eastern European Restaurant   
1            Donut Shop             Drugstore  Eastern European Restaurant   
2        Medical Center          Intersection                Women's Store   
3        Medical Center          Intersection                Women's Store   
4        Medical Center          Intersection                Women's Store   

  10th Most Common Venue  
0    Dumpling Restaurant  
1               Festival  
2                Dog Run  
3                Dog Run  
4                Dog Run

**Finally visualize the 5 cluster types color coded & displayed (overlaid) on a Folium Map**

In [35]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

**Notice how the parks & recreational areas (teal blue markers) are all assigned to one type of clusters**

### This concludes part 3 of the assignment.   